# Lumber transportation problem (J. Reeb and S. Leavengood)

Millco has three wood mills and is planning three new logging sites. Each mill has a maximum capacity and each logging site can harvest a certain number of truckloads of lumber per day. The cost of a haul is \$2/mile of distance. If distances from logging sites to mills are given below, how should the hauls be routed to minimize hauling costs while meeting all demands?

| Logging Site | Mill A | Mill B | Mill C | Max loads per day |
|:------------:|:------:|:------:|:------:|:-----------------:|
| 1            |  8     |  15    |  50    |  20               |
| 2            |  10    |  17    |  20    |  30               |
| 3            |  30    |  26    |  15    |  45               |
| Mill demand  |  30    |  35    |  30    |                   |

In [1]:
%reload_ext gams.magic

In [2]:
import numpy as np
m = gams.exchange_container

# Model sets and parameters
sites = m.addSet('sites', records = ["1", "2", "3"])
mills = m.addSet('mills', records = ["Mill A","Mill B", "Mill C"])
dist = m.addParameter('dist', [sites, mills], records = np.array([[ 8,15,50],
                                                                  [10,17,20],
                                                                  [30,26,15]]))
supply = m.addParameter('supply', [sites], records = np.array([20,30,45]))
demand = m.addParameter('demand', [mills], records = np.array([30,35,30]))
cost_per_haul = m.addParameter('cost_per_haul', records = 4)

# Model variables
m.addAlias('s',sites)
m.addAlias('m', mills)
ship = m.addVariable('ship', 'positive', [sites, mills])
obj = m.addVariable('obj', 'free')

In [3]:
%%gams 
# GAMS Model
Equation defcost;   defcost..      cost_per_haul*sum((s,m), ship(s,m)*dist(s,m)) =e= obj;
Equation defsupply; defsupply(s).. sum(m, ship(s,m)) =e= supply(s);
Equation defdemand; defdemand(m).. sum(s, ship(s,m)) =e= demand(m);

model millco / all /;

In [4]:
%gams solve millco min obj using lp;

Solver Status        Model Status  Objective #equ #var Model Type Solver  \
0    Normal (1)  Optimal Global (1)     5760.0    7   10         LP  CPLEX   

  Solver Time  
0           0

In [5]:
display(m["ship"].pivot())
print(f'Total cost will be {obj.records["level"][0]}')

Mill A  Mill B  Mill C
1     0.0    20.0     0.0
2    30.0     0.0     0.0
3     0.0    15.0    30.0

Total cost will be 5760.0


In [6]:
gams.create('genmodel')
m = gams.exchange_container

# Generic Model sets and parameters
i = m.addSet('i', records = ['i'+str(i) for i in range(6)], description = 'equation index')
j = m.addSet('j', records = ['j'+str(j) for j in range(9)], description = 'variable index')
A = m.addParameter('A', [i,j], records = np.array([[1,1,1,0,0,0,0,0,0],
                                                   [0,0,0,1,1,1,0,0,0],
                                                   [0,0,0,0,0,0,1,1,1],
                                                   [1,0,0,1,0,0,1,0,0],
                                                   [0,1,0,0,1,0,0,1,0],
                                                   [0,0,1,0,0,1,0,0,1]]))
b = m.addParameter('b', [i], records = np.array([20,30,45,30,35,30]))
c = m.addParameter('c', [j], records = np.array([8,15,50,10,17,20,30,26,15]))
x = m.addVariable('x', 'positive', [j])
obj = m.addVariable('obj', 'free')

In [7]:
%%gams
# Generic GAMS Model
Equation defobj; defobj.. 4*sum(j, c(j)*x(j)) =e= obj;
Equation e(i);   e(i)..   sum(j, A(i,j)*x(j)) =e= b(i);

model gen / all /;

In [8]:
%gams solve gen min obj using lp;

Solver Status        Model Status  Objective #equ #var Model Type Solver  \
0    Normal (1)  Optimal Global (1)     5760.0    7   10         LP  CPLEX   

  Solver Time  
0           0

In [9]:
display(x.records)
print(f'Total cost will be {obj.records["level"][0]}')

j  level  marginal  lower  upper  scale
0  j0    0.0      -0.0    0.0    inf    1.0
1  j1   20.0       0.0    0.0    inf    1.0
2  j2    0.0     184.0    0.0    inf    1.0
3  j3   30.0       0.0    0.0    inf    1.0
4  j4    0.0       0.0    0.0    inf    1.0
5  j5    0.0      56.0    0.0    inf    1.0
6  j6    0.0      44.0    0.0    inf    1.0
7  j7   15.0       0.0    0.0    inf    1.0
8  j8   30.0       0.0    0.0    inf    1.0

Total cost will be 5760.0


In [10]:
%gams_cleanup --closedown